In [1]:
import pandas as pd
import requests
from datetime import datetime

get the list of movies

In [2]:
df_raw = pd.read_excel('data\\titles.xlsx')

var_symbols = ["~", "!", "@", "#", "$", "%", "^", "&", "*", "(", 
                ")", "_", "+", "`", "-", "=", "[", "]", "\\", "{", 
                "}", "|", ";", "'", ":", '"', ",", ".", "/", "<", ">", "?", "  "]

df_titles = pd.DataFrame()
for i, row in df_raw.iterrows():
    var_tmp_title=str(row['Title'])
    var_tmp_year=row['Year']
    var_tmp_title = var_tmp_title.encode('ascii',errors='ignore').decode() #remove non ascii characters
    var_tmp_title = var_tmp_title.lower() #lower everything

    for i in var_symbols:
        var_tmp_title = var_tmp_title.replace(i, ' ') #replace all the symbols with a space

    new_row = {'Year':var_tmp_year, 'Title':var_tmp_title}
    df_titles = pd.concat([df_titles, pd.DataFrame([new_row])], ignore_index=True) 


define the function to get data from chatgpt

In [3]:
service = "chatgpt-api7.p.rapidapi.com"
url = "https://"+service+"/ask"

headers = {
    "content-type": "application/json",
    "X-RapidAPI-Key": "fd431d27a1mshb7f204feaf87f9ap1b4d99jsnea3e660b29f6",
    "X-RapidAPI-Host": service
}
def get_gpt_data(command):
   
    payload = {"query": command}
    
    response = requests.request("POST", url, json=payload, headers=headers)
    var = response.json().get("response")
    return var

get the summary and plot for the movie title

In [4]:

df_data = pd.DataFrame()
command1 = "give me the plot for the movie \""
command2 = "\" released in the year "
command3 = ".write it in 20 words. write everything in 1 paragraph. dont use the \" mark in your answer"
command4 = "dont use a \" mark and write a 5 word summary for: "
counter=0
whentowrite = 5000

for i, row in df_titles.iterrows():
        try:
                var_title=str(row['Title'])
                var_year=row['Year']

                command = (command1+str(var_title)+command2+str(var_year)+command3).lower()
                var_plot = get_gpt_data(command)

                command = (command4+str(var_plot)).lower()
                var_summary = get_gpt_data(command)

                new_row = {'Year':var_year, 'Title':var_title, 'Plot':var_plot, 'Summary':var_summary}
                df_data = pd.concat([df_data, pd.DataFrame([new_row])], ignore_index=True)
                counter+=1
                print(str(counter)+' - '+str(var_title)+' - '+str(var_summary)+' - '+str(var_plot))
                if counter >= whentowrite:
                        dt_string = datetime.now().strftime("%Y%m%d%H%M%S")
                        df_data.to_excel('data\\downloaded_data_'+dt_string+'.xlsx')
                        print('downloaded_data_'+dt_string+'.xlsx')
                        df_data = pd.DataFrame()
                        counter = 0
        except Exception as error:
                print(str(var_title)+' - errored')
                pass


1 - end play - Struggling artists battle for inheritance. - End Play is a 1975 movie about a couple of struggling artists who are forced to move in with their uncle. They soon find themselves battling for the family’s inheritance and discovering a deep bond with their uncle.
2 - end play - Young people confront fears, learn life's complexities. - End Play is a 1976 drama about a group of young people who, while in the midst of an existential crisis, are forced to confront their fears and fight for their future. They cross paths with a professor who helps them understand life’s complexities and encourages them to make the right decisions.
3 - raw deal - FBI agent infiltrates mob, betrays. - Raw Deal is a 1977 American action crime thriller film about an FBI agent who goes undercover as a mobster to infiltrate the Chicago Outfit and steal incriminating evidence against them. He soon finds himself in a difficult situation when he is betrayed by a corrupt cop and must fight to protect his 

In [ ]:
dt_string = datetime.now().strftime("%Y%m%d%H%M%S")
df_data.to_excel('data\\downloaded_data_'+dt_string+'.xlsx')